In [ ]:
GRU 는 게이트 순환 유닛이라고도 하면 LSTM의 셀을 간소화 시킨구조

따로 셀 상태를 두지 않고 단순 순환 신경망과 마찬가지로 하나의 출력만이 존재하지만
이 출력이 셀상태처럼 장기 의존성문제를 해결할수있는 능력이있음.

이를위해 게이트제어기를 이용해, 망각게이트,입력게이트 모두제어.

그리고 리셋게이트(reset gate) , 갱신 게이트(update gate) 로 GRU 셀 두개의 게이트로 구성 

GRU = 유닛수가 무지막지하게 많아져서 서로역할분할도 많아지면서 순환신경망을 구성 


In [1]:
# GRU 실습
import numpy as np
import pandas as pd
import os

basepath = 'C:/Users/PC/Desktop/Carlos/aclImdb/aclImdb'  # 영화 리뷰 데이터셋을 로드하고 전처리하는 과정

labels = {'pos': 1, 'neg': 0} #변수에 긍정('pos')과 부정('neg') 레이블에 대한 매핑을 정의 
df = pd.DataFrame()
for s in ('test', 'train'): #이중 for 루프를 사용하여 'test'와 'train' 폴더, 그리고 'pos'와 'neg' 폴더에 접근
    for l in ('pos', 'neg'):
        path = os.path.join(basepath, s, l) #함수를 사용하여 파일 경로를 생성
        for file in sorted(os.listdir(path)):# 해당 경로의 파일들을 정렬
            with open(os.path.join(path, file), 
                      'r', encoding='utf-8') as infile:
                txt = infile.read()
            # df = df.append([[txt, labels[l]]],   #데이터프레임에 리뷰 내용(txt)과 해당하는 레이블(labels[l])을 추가
            #                ignore_index=True)  #이거 더이상사용안됨.
            df = pd.concat([df, pd.DataFrame([[txt, labels[l]]])]) #concat으로 대체
        
df.columns = ['review', 'sentiment']

In [2]:
X = df["review"].values
y = df["sentiment"].values 

In [3]:
X

array(["I went and saw this movie last night after being coaxed to by a few friends of mine. I'll admit that I was reluctant to see it because from what I knew of Ashton Kutcher he was only able to do comedy. I was wrong. Kutcher played the character of Jake Fischer very well, and Kevin Costner played Ben Randall with such professionalism. The sign of a good movie is that it can toy with our emotions. This one did exactly that. The entire theater (which was sold out) was overcome by laughter during the first half of the movie, and were moved to tears during the second half. While exiting the theater I not only saw many women in tears, but many full grown men as well, trying desperately not to let anyone see them crying. This movie was great, and I suggest that you go see it before you judge.",
       'Actor turned director Bill Paxton follows up his promising debut, the Gothic-horror "Frailty", with this family friendly sports drama about the 1913 U.S. Open where a young American caddy

In [4]:
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences #문장이 일찍끝나면 뒤에 공백을 채워서(실제론 0으로채움) , 글자길이를 맞춤. 
tokenizer = Tokenizer()
tokenizer.fit_on_texts(X)

In [5]:
tokenizer.word_index # 젤 많은 순서대로 숫자를 매김 ex) the 가 젤많이 나와서 1 , and 가 2번째로 젤많이 나와서 2로 , 이렇게 약속.

{'the': 1,
 'and': 2,
 'a': 3,
 'of': 4,
 'to': 5,
 'is': 6,
 'br': 7,
 'in': 8,
 'it': 9,
 'i': 10,
 'this': 11,
 'that': 12,
 'was': 13,
 'as': 14,
 'for': 15,
 'with': 16,
 'movie': 17,
 'but': 18,
 'film': 19,
 'on': 20,
 'not': 21,
 'you': 22,
 'are': 23,
 'his': 24,
 'have': 25,
 'be': 26,
 'one': 27,
 'he': 28,
 'all': 29,
 'at': 30,
 'by': 31,
 'an': 32,
 'they': 33,
 'so': 34,
 'who': 35,
 'from': 36,
 'like': 37,
 'or': 38,
 'just': 39,
 'her': 40,
 'out': 41,
 'about': 42,
 'if': 43,
 "it's": 44,
 'has': 45,
 'there': 46,
 'some': 47,
 'what': 48,
 'good': 49,
 'when': 50,
 'more': 51,
 'very': 52,
 'up': 53,
 'no': 54,
 'time': 55,
 'my': 56,
 'even': 57,
 'would': 58,
 'she': 59,
 'which': 60,
 'only': 61,
 'really': 62,
 'see': 63,
 'story': 64,
 'their': 65,
 'had': 66,
 'can': 67,
 'me': 68,
 'well': 69,
 'were': 70,
 'than': 71,
 'much': 72,
 'we': 73,
 'bad': 74,
 'been': 75,
 'get': 76,
 'do': 77,
 'great': 78,
 'other': 79,
 'will': 80,
 'also': 81,
 'into': 82,
 'p

In [6]:
#문장이 숫자로 변경됨. 
X_tk = tokenizer.texts_to_sequences(X)
X_tk

[[10,
  414,
  2,
  210,
  11,
  17,
  238,
  316,
  100,
  109,
  29378,
  5,
  31,
  3,
  171,
  350,
  4,
  1767,
  657,
  986,
  12,
  10,
  13,
  5719,
  5,
  63,
  9,
  84,
  36,
  48,
  10,
  677,
  4,
  10168,
  10169,
  28,
  13,
  61,
  480,
  5,
  77,
  202,
  10,
  13,
  356,
  10169,
  253,
  1,
  108,
  4,
  3639,
  16387,
  52,
  69,
  2,
  1650,
  8161,
  253,
  1220,
  8602,
  16,
  138,
  11311,
  1,
  2015,
  4,
  3,
  49,
  17,
  6,
  12,
  9,
  67,
  3006,
  16,
  260,
  1334,
  11,
  27,
  115,
  621,
  12,
  1,
  438,
  769,
  60,
  13,
  2983,
  41,
  13,
  3225,
  31,
  2150,
  300,
  1,
  86,
  303,
  4,
  1,
  17,
  2,
  70,
  1652,
  5,
  1723,
  300,
  1,
  336,
  303,
  136,
  11798,
  1,
  769,
  10,
  21,
  61,
  210,
  106,
  378,
  8,
  1723,
  18,
  106,
  363,
  2079,
  345,
  14,
  69,
  264,
  2817,
  21,
  5,
  379,
  250,
  63,
  93,
  2492,
  11,
  17,
  13,
  78,
  2,
  10,
  1472,
  12,
  22,
  139,
  63,
  9,
  159,
  22,
  1717],
 [291,
  66

In [7]:
#여기에 문장이 1개씩들어있는데 for문써서 Token화된것들 하나씩나오게함
max_len = max([len(s)for s in X_tk])
max_len #제일 길이가 긴문장이 2493임. 이것과 길이를 같게 해줌. (나머지는 전부 0 으로 )

2493

In [8]:
X_sq = pad_sequences(X_tk, maxlen = max_len, padding="pre") #번역기에 최대 글자수가 있는 이유가 이것 때문임.     #padding ="pre" -> 순환신경망 계통은 앞에 패딩 해야함.
#순환신경망에는 앞부분에 padding을 해줘야하고 Transformer는 뒷부분에 Padding 을해줘야함. 

#RNN은 왜 앞쪽에 붙여야하나? -> 순환신경망보면 매step 들어감, -> 마지막 출력이 젤중요함 (최종출력이 문장전체의 문맥이니깐) 
#ex) "I am student" 라했을때 maxlen 가 8 이면 I -> 1 , am ->2 , student ->3 이고 나머지는 0 , 0, ,0.. 으로되는데 그러면서 앞에것이 사라지기때문.(정보손실때문에)
#뒤로갈수록 앞쪽의 정보가 희미해지기 때문 . 

X_sq

array([[    0,     0,     0, ...,   159,    22,  1717],
       [    0,     0,     0, ...,   165,    32,   309],
       [    0,     0,     0, ...,    98,    25,   407],
       ...,
       [    0,     0,     0, ...,    17,    96,    74],
       [    0,     0,     0, ..., 71508,  1218,   793],
       [    0,     0,     0, ...,    11,     6,  1376]])

In [9]:
X_sq.shape

(50000, 2493)

In [10]:
vocab_size = len(tokenizer.word_index)+1


In [11]:
from sklearn.model_selection import train_test_split
X_train , X_test , y_train, y_test = train_test_split(X_sq , y ,
                                                      test_size=0.2,
                                                      shuffle= True,
                                                      random_state= 0)

print(X_train.shape, y_train.shape)
print(X_test.shape , y_test.shape)


(40000, 2493) (40000,)
(10000, 2493) (10000,)


In [12]:
from tensorflow.keras import layers
from tensorflow.keras import Model

#body 입력을 어떻게 받아들여서 정보를 압축할것인지.
inputs = layers.Input(shape=(max_len,))


x = layers.Embedding(vocab_size, 128 , embeddings_regularizer = "l2")(inputs)
x = layers.GRU(units = 128 , return_sequences = True)(x)
x = layers.GRU(units = 64 , return_sequences = True)(x)
x = layers.GRU(units = 64 , return_sequences = False)(x)

#Header 바디가 압축한 정보를 가지고 출력과 어떻게 마출지, Y데이터와 어떻게 마출지. 정답이 뭔지 . 
layers.Dense(32, activation = "relu")(x)
outputs = layers.Dense(1, activation = "sigmoid" )(x)

model = Model(inputs = inputs , outputs = outputs)
model.compile(optimizer="adam", loss="binary_crossentropy" , metrics=["acc"]) # mse -> 회귀문제에 쓰임,  binary_crossentropy -> 이진 분류문제를 만들때. 0,1  / metrics acc-> accuracy
model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 2493)]            0         
                                                                 
 embedding (Embedding)       (None, 2493, 128)         15904384  
                                                                 
 gru (GRU)                   (None, 2493, 128)         99072     
                                                                 
 gru_1 (GRU)                 (None, 2493, 64)          37248     
                                                                 
 gru_2 (GRU)                 (None, 64)                24960     
                                                                 
 dense_1 (Dense)             (None, 1)                 65        
                                                                 
Total params: 16,065,729
Trainable params: 16,065,729
Non-tra

In [13]:
from tensorflow.keras.callbacks import EarlyStopping
es_callback = EarlyStopping(monitor="val_loss", patience = 10 , restore_best_weights = True)
history = model.fit( X_train, y_train , 
          batch_size = 64 ,
          epochs = 300 ,
          validation_split = 0.2 ,
          callbacks=[es_callback] )
#GPU가 2의 제곱승으로밖에 이해를 못해서 batch_size를 2의 제곱으로 해줘야함.


Epoch 1/300
500/500 [==============================] - 181s 357ms/step - loss: 4.3945 - acc: 0.7362 - val_loss: 0.7055 - val_acc: 0.7826
Epoch 2/300
500/500 [==============================] - 179s 357ms/step - loss: 0.6177 - acc: 0.8272 - val_loss: 0.5571 - val_acc: 0.8645
Epoch 3/300
500/500 [==============================] - 179s 358ms/step - loss: 0.5388 - acc: 0.8691 - val_loss: 0.5004 - val_acc: 0.8816
Epoch 4/300
500/500 [==============================] - 179s 358ms/step - loss: 0.4770 - acc: 0.8910 - val_loss: 0.4587 - val_acc: 0.8895
Epoch 5/300
500/500 [==============================] - 177s 354ms/step - loss: 0.4454 - acc: 0.8997 - val_loss: 0.4402 - val_acc: 0.8984
Epoch 6/300
500/500 [==============================] - 177s 355ms/step - loss: 0.4342 - acc: 0.9048 - val_loss: 0.4464 - val_acc: 0.8925
Epoch 7/300
500/500 [==============================] - 195s 390ms/step - loss: 0.4197 - acc: 0.9087 - val_loss: 0.4250 - val_acc: 0.9038
Epoch 8/300
500/500 [====================

In [17]:
model.save("models/sentiment_gru.h5")

In [18]:
model.evaluate(X_test, y_test) 

313/313 [==============================] - 41s 130ms/step - loss: 0.4037 - acc: 0.9077


[0.4036703407764435, 0.9077000021934509]

In [19]:
model.predict(X_test) #-> 

313/313 [==============================] - 40s 127ms/step


array([[0.8794731 ],
       [0.00297495],
       [0.00303954],
       ...,
       [0.25374612],
       [0.97876614],
       [0.08353359]], dtype=float32)

In [ ]:

#transformer는 따로 수업하지않기때문에 따로배울려면 여기서 (교수님추천)

https://wikidocs.net/31379 

15. 어텐션 매커니즘 ~ 보면 트랜스포머 배울수있음

진짜로 전향할거면 디퓨전모델도 해야함